# Integrating RxAPI to Populate different fields for Catalog Products

In [2]:
import pandas as pd
import requests
import time

In [ ]:
data_df = pd.read_csv("/catalog_data.csv", on_bad_lines='skip')

In [ ]:
data_df.head()

ProductId  SourceProductId          ProductName  \
0       2607       10002632.0  Actrapid HM Penfill   
1       3447       10003952.0              Donep M   
2       3447       10003952.0              Donep M   
3       8027       10005601.0              Lidocam   
4       8027       10005601.0              Lidocam   

                                         DisplayName  \
0  Actrapid HM Penfill 100 IU Injection 3 ml Cart...   
1                            Donep M Tablet (10 Tab)   
2                            Donep M Tablet (10 Tab)   
3                          Lidocam Mouth Wash 120 ml   
4                          Lidocam Mouth Wash 120 ml   

                        SaltName                            MfgGroup  
0  Human Insulin/Soluble Insulin  Abbott India Limited(Novo Nordisk)  
1                      Memantine                  ALKEM LABORATORIES  
2                      Donepezil                  ALKEM LABORATORIES  
3                    Benzoxonium               AJANTA PHARMA LIMITED  
4                      Lidocaine               AJANTA PHARMA LIMITED

## Integrating RxClass API 

This API is used to fetch different information - such as the diseases that may be treated by the drug, the ATC information, the information pertaining to physiological effects.
We pass the drug name in the API. We use the source as MEDRT (which is one of the data sources used by the NLM).

In [ ]:
API_REQUEST_RXCLASS_ENDPOINT = 'https://rxnav.nlm.nih.gov/'
API_REQUEST_RXCLASS_PARAMS = 'REST/rxclass/class/byDrugName.json?drugName={value}&relaSource={source}&relas={relation}'

API_LATENCY_ASSUMED = 0.002       # Assuming roughly 2ms latency on the API and network
API_THROTTLE_WAIT = (1.0/100.0)-API_LATENCY_ASSUMED

MEDS_CLASS_PARAMS_TEMPLATE = {
    "value": "",
    "source": "MEDRT",
    "relation":"may_treat"
}

In [ ]:
def request_class(drug_name,
                  source_name,
                  drug_relation,
                  endpoint_url = API_REQUEST_RXCLASS_ENDPOINT, 
                  endpoint_params = API_REQUEST_RXCLASS_PARAMS,
                  request_template = MEDS_CLASS_PARAMS_TEMPLATE):
    # Make sure we have an article title
    if not drug_name: 
      print ("NO name")
      return None
    
    # Titles are supposed to have spaces replaced with "_" and be URL encoded
    drug_name_encoded = drug_name.replace(' ','%20')
    request_template['value'] = drug_name_encoded
    request_template['source'] = source_name
    request_template['relation'] = drug_relation
    
    # now, create a request URL by combining the endpoint_url with the parameters for the request
    request_url = endpoint_url+endpoint_params.format(**request_template)
    print(request_url)
    
    # make the request
    try:
        # we'll wait first, to make sure we don't exceed the limit in the situation where an exception
        # occurs during the request processing - throttling is always a good practice with a free
        # data source like Wikipedia - or other community sources
        if API_THROTTLE_WAIT > 0.0:
            time.sleep(API_THROTTLE_WAIT)
        response = requests.get(request_url)
        json_response = response.json()
        
    except Exception as e:
        print(e)
        json_response = None
    return json_response

### Creating a map for the diseases treated by each salt - salt is the key and the set of diseases treated by it are the value

In [ ]:
salt_map = {}

for index, row in data_df.iterrows():
  if salt_map.__contains__(row["SaltName"]) == False:
    disease = set()
    response = request_class(str(row["SaltName"]), 'MEDRT', 'may_treat')
    if response != {}:
      print(response)
      for obj in response['rxclassDrugInfoList']['rxclassDrugInfo']:
        disease.add(obj['rxclassMinConceptItem']['className'])
    salt_map[row["SaltName"]]=disease
    

Streaming output truncated to the last 5000 lines.
{'rxclassDrugInfoList': {'rxclassDrugInfo': [{'minConcept': {'rxcui': '1298831', 'name': 'tiotropium bromide monohydrate', 'tty': 'PIN'}, 'rxclassMinConceptItem': {'classId': 'D011656', 'className': 'Pulmonary Emphysema', 'classType': 'DISEASE'}, 'rela': 'may_treat', 'relaSource': 'MEDRT'}, {'minConcept': {'rxcui': '1298831', 'name': 'tiotropium bromide monohydrate', 'tty': 'PIN'}, 'rxclassMinConceptItem': {'classId': 'D029481', 'className': 'Bronchitis, Chronic', 'classType': 'DISEASE'}, 'rela': 'may_treat', 'relaSource': 'MEDRT'}, {'minConcept': {'rxcui': '1552007', 'name': 'tiotropium bromide mono', 'tty': 'PIN'}, 'rxclassMinConceptItem': {'classId': 'D011656', 'className': 'Pulmonary Emphysema', 'classType': 'DISEASE'}, 'rela': 'may_treat', 'relaSource': 'MEDRT'}, {'minConcept': {'rxcui': '1552007', 'name': 'tiotropium bromide mono', 'tty': 'PIN'}, 'rxclassMinConceptItem': {'classId': 'D029481', 'className': 'Bronchitis, Chronic', 

In [ ]:
disease = set()
resp_thx = response_Thyroxine['rxclassDrugInfoList']['rxclassDrugInfo']
for view in resp_thx:
  disease.add(view['rxclassMinConceptItem']['className'])

print(disease)


{'Myxedema', 'Thyroid Neoplasms', 'Goiter', 'Thyrotoxicosis', 'Thyroiditis, Autoimmune'}


In [ ]:
print(salt_map)

{'Thyroxine': {'Thyrotoxicosis', 'Myxedema', 'Thyroiditis, Autoimmune', 'Thyroid Neoplasms', 'Goiter'}, 'Teneligliptin': set(), 'Metformin': {'Diabetes Mellitus, Type 2'}, 'Nebivolol': {'Hypertension, Malignant'}, 'Amlodipine': {'Coronary Artery Disease', 'Angina Pectoris, Variant', 'Hypertension'}, 'Telmisartan': {'Heart Failure', 'Diabetic Nephropathies', 'Ventricular Dysfunction, Left', 'Hypertension'}, 'Chlorthalidone': {'Heart Failure', 'Hypertension', 'Edema', 'Liver Cirrhosis', 'Glomerulonephritis', 'Nephrotic Syndrome', 'Renal Insufficiency'}, 'Hydrochlorothiazide': {'Heart Failure', 'Nephrotic Syndrome', 'Hypertension', 'Edema'}, 'Luliconazole': {'Tinea'}, 'Olanzapine': {'Bipolar Disorder', 'Psychotic Disorders', 'Schizophrenia'}, 'Pregabalin': {'Fibromyalgia', 'Spinal Cord Injuries', 'Neuralgia, Postherpetic', 'Seizures'}, 'Mecobalamin': {'Multiple Sclerosis', 'Alcoholic Neuropathy', 'Diabetic Neuropathies', 'Anemia, Pernicious'}, 'Folic Acid': {'Anemia, Megaloblastic', 'Foli

In [ ]:
print(len(salt_map))

3854


### Populating the disease_may_treat column using the salt_map

In [ ]:
disease_may_treat = []
for index, row in data_df.iterrows():
  if salt_map.__contains__(row["SaltName"]) == True:
    disease_may_treat.append(salt_map[row["SaltName"]]) 

data_df["disease_may_treat"] = disease_may_treat

In [ ]:
data_df.head(20)

ProductId  SourceProductId           ProductName  \
0        2607       10002632.0   Actrapid HM Penfill   
1        3447       10003952.0               Donep M   
2        3447       10003952.0               Donep M   
3        8027       10005601.0               Lidocam   
4        8027       10005601.0               Lidocam   
5       14973       10014311.0               Comoist   
6       42842       10030342.0               Warclav   
7       42842       10030342.0               Warclav   
8       74360       10049404.0                 Mlobe   
9       78551       10053597.0  Oligocare Forte Plus   
10      78551       10053597.0  Oligocare Forte Plus   
11      81790       10056825.0               Dicewin   
12     107402       10081637.0                Mirtee   
13     117379       10090335.0              Clofiron   
14     117379       10090335.0              Clofiron   
15     117379       10090335.0              Clofiron   
16     117379       10090335.0              Clofiron   
17       1799       10001846.0                 Tiova   
18       2088       10002332.0        Glucored Forte   
19       2088       10002332.0        Glucored Forte   

                                          DisplayName  \
0   Actrapid HM Penfill 100 IU Injection 3 ml Cart...   
1                             Donep M Tablet (10 Tab)   
2                             Donep M Tablet (10 Tab)   
3                           Lidocam Mouth Wash 120 ml   
4                           Lidocam Mouth Wash 120 ml   
5                             Comoist Eye Drops 10 ml   
6                      Warclav 625 mg Tablet (10 Tab)   
7                      Warclav 625 mg Tablet (10 Tab)   
8                             Mlobe Eye Ointment 5 gm   
9                Oligocare Forte Plus Tablet (15 Tab)   
10               Oligocare Forte Plus Tablet (15 Tab)   
11                           Dicewin Capsule (10 Cap)   
12                       Mirtee 30 mg Tablet (10 Tab)   
13                           Clofiron Tablet (10 Tab)   
14                           Clofiron Tablet (10 Tab)   
15                           Clofiron Tablet (10 Tab)   
16                           Clofiron Tablet (10 Tab)   
17                                      Tiova Inhaler   
18                     Glucored Forte Tablet (10 Tab)   
19                     Glucored Forte Tablet (10 Tab)   

                         SaltName                            MfgGroup  \
0   Human Insulin/Soluble Insulin  Abbott India Limited(Novo Nordisk)   
1                       Memantine                  ALKEM LABORATORIES   
2                       Donepezil                  ALKEM LABORATORIES   
3                     Benzoxonium               AJANTA PHARMA LIMITED   
4                       Lidocaine               AJANTA PHARMA LIMITED   
5   Hydroxypropyl Methylcellulose                  KLAR SEHEN PVT LTD   
6                     Amoxycillin                      Pfizer Limited   
7                 Clavulanic Acid                      Pfizer Limited   
8                    Moxifloxacin       Sapient Laboratorises Pvt Ltd   
9                    Coenzyme Q10            Meyer Organics Pvt. Ltd.   
10                    Combination            Meyer Organics Pvt. Ltd.   
11                      Diacerein       T Banko Genic Pharmaceuticals   
12                    Mirtazapine                        TALENT INDIA   
13              Sodium Feredetate             KLOSTER PHARMACEUTICALS   
14                     Folic Acid             KLOSTER PHARMACEUTICALS   
15                    Vitamin B12             KLOSTER PHARMACEUTICALS   
16                 Zinc Gluconate             KLOSTER PHARMACEUTICALS   
17                     Tiotropium                       Cipla Ltd.(M)   
18                  Glibenclamide        Sun Pharma Laboratories Ltd.   
19                      Metformin        Sun Pharma Laboratories Ltd.   

                                    disease_may_treat  
0                                      

## RxClass API Call for ATC information

In [ ]:
API_REQUEST_RXCLASS_ATC_ENDPOINT = 'https://rxnav.nlm.nih.gov/'
API_REQUEST_RXCLASS_ATC_PARAMS = 'REST/rxclass/class/byDrugName.json?drugName={value}&relaSource={source}'

API_LATENCY_ASSUMED = 0.002       # Assuming roughly 2ms latency on the API and network
API_THROTTLE_WAIT = (1.0/100.0)-API_LATENCY_ASSUMED

MEDS_CLASS_ATC_PARAMS_TEMPLATE = {
    "value": "",
    "source": "ATC"
}

In [ ]:
def request_ATC_class(drug_name,
                  source_name,
                  endpoint_url = API_REQUEST_RXCLASS_ATC_ENDPOINT, 
                  endpoint_params = API_REQUEST_RXCLASS_ATC_PARAMS,
                  request_template = MEDS_CLASS_ATC_PARAMS_TEMPLATE):
    # Make sure we have an article title
    if not drug_name: 
      print ("NO name")
      return None
    
    # Titles are supposed to have spaces replaced with "_" and be URL encoded
    drug_name_encoded = drug_name.replace(' ','%20')
    request_template['value'] = drug_name_encoded
    request_template['source'] = source_name
    
    # now, create a request URL by combining the endpoint_url with the parameters for the request
    request_url = endpoint_url+endpoint_params.format(**request_template)
    print(request_url)
    
    # make the request
    try:
        # we'll wait first, to make sure we don't exceed the limit in the situation where an exception
        # occurs during the request processing - throttling is always a good practice with a free
        # data source like Wikipedia - or other community sources
        if API_THROTTLE_WAIT > 0.0:
            time.sleep(API_THROTTLE_WAIT)
        response = requests.get(request_url)
        json_response = response.json()
        
    except Exception as e:
        print(e)
        json_response = None
    return json_response

In [ ]:
response_MESH = request_ATC_class('amlodipine', 'MESH')

https://rxnav.nlm.nih.gov/REST/rxclass/class/byDrugName.json?drugName=amlodipine&relaSource=MESH


In [ ]:
response_ATC = request_ATC_class('amlodipine', "ATC")

https://rxnav.nlm.nih.gov/REST/rxclass/class/byDrugName.json?drugName=amlodipine&relaSource=ATC


### Creating atc_map to populate ATC information for each salt name with salt as key and atc as value

In [ ]:
atc_map = {}

for index, row in data_df.iterrows():
  if atc_map.__contains__(row["SaltName"]) == False:
    atc = set()
    response = request_ATC_class(str(row["SaltName"]), 'ATC')
    if response != {}:
      print(response)
      for obj in response['rxclassDrugInfoList']['rxclassDrugInfo']:
        atc.add(obj['rxclassMinConceptItem']['className'])
    atc_map[row["SaltName"]]=atc

Streaming output truncated to the last 5000 lines.
{'rxclassDrugInfoList': {'rxclassDrugInfo': [{'minConcept': {'rxcui': '3289', 'name': 'dextromethorphan', 'tty': 'IN'}, 'rxclassMinConceptItem': {'classId': 'R05DA', 'className': 'Opium alkaloids and derivatives', 'classType': 'ATC1-4'}, 'rela': '', 'relaSource': 'ATC'}]}}
https://rxnav.nlm.nih.gov/REST/rxclass/class/byDrugName.json?drugName=Levocetirizine&relaSource=ATC
{'rxclassDrugInfoList': {'rxclassDrugInfo': [{'minConcept': {'rxcui': '356887', 'name': 'levocetirizine', 'tty': 'IN'}, 'rxclassMinConceptItem': {'classId': 'R06AE', 'className': 'Piperazine derivatives', 'classType': 'ATC1-4'}, 'rela': '', 'relaSource': 'ATC'}]}}
https://rxnav.nlm.nih.gov/REST/rxclass/class/byDrugName.json?drugName=Montelukast&relaSource=ATC
{'rxclassDrugInfoList': {'rxclassDrugInfo': [{'minConcept': {'rxcui': '88249', 'name': 'montelukast', 'tty': 'IN'}, 'rxclassMinConceptItem': {'classId': 'R03DC', 'className': 'Leukotriene receptor antagonists', 'c

### Populating the atc column using the atc_map

In [ ]:
atc = []
for index, row in data_df.iterrows():
  if atc_map.__contains__(row["SaltName"]) == True:
    atc.append(atc_map[row["SaltName"]]) 

data_df["atc"] = atc

### RxClass API Call for Pharmacological Actions information

In [ ]:
mesh_map = {}

for index, row in data_df.iterrows():
  if mesh_map.__contains__(row["SaltName"]) == False:
    mesh = set()
    response = request_ATC_class(str(row["SaltName"]), 'MESH')
    if response != {}:
      print(response)
      for obj in response['rxclassDrugInfoList']['rxclassDrugInfo']:
        mesh.add(obj['rxclassMinConceptItem']['className'])
    mesh_map[row["SaltName"]]=mesh

Streaming output truncated to the last 5000 lines.
https://rxnav.nlm.nih.gov/REST/rxclass/class/byDrugName.json?drugName=Water%20Bottle&relaSource=MESH
https://rxnav.nlm.nih.gov/REST/rxclass/class/byDrugName.json?drugName=Levetiracetam&relaSource=MESH
{'rxclassDrugInfoList': {'rxclassDrugInfo': [{'minConcept': {'rxcui': '114477', 'name': 'levetiracetam', 'tty': 'IN'}, 'rxclassMinConceptItem': {'classId': 'D000927', 'className': 'Anticonvulsants', 'classType': 'MESHPA'}, 'rela': '', 'relaSource': 'MESH'}, {'minConcept': {'rxcui': '114477', 'name': 'levetiracetam', 'tty': 'IN'}, 'rxclassMinConceptItem': {'classId': 'D018697', 'className': 'Nootropic Agents', 'classType': 'MESHPA'}, 'rela': '', 'relaSource': 'MESH'}]}}
https://rxnav.nlm.nih.gov/REST/rxclass/class/byDrugName.json?drugName=Glutathione&relaSource=MESH
https://rxnav.nlm.nih.gov/REST/rxclass/class/byDrugName.json?drugName=Dextromethorphan&relaSource=MESH
{'rxclassDrugInfoList': {'rxclassDrugInfo': [{'minConcept': {'rxcui': '10

### Populating the Pharmacological Actions column using the mesh_map

In [ ]:
mesh = []
for index, row in data_df.iterrows():
  if mesh_map.__contains__(row["SaltName"]) == True:
    mesh.append(mesh_map[row["SaltName"]]) 

data_df["Pharmacological Actions"] = mesh

In [ ]:
data_df.head(20)

ProductId  SourceProductId           ProductName  \
0        2607       10002632.0   Actrapid HM Penfill   
1        3447       10003952.0               Donep M   
2        3447       10003952.0               Donep M   
3        8027       10005601.0               Lidocam   
4        8027       10005601.0               Lidocam   
5       14973       10014311.0               Comoist   
6       42842       10030342.0               Warclav   
7       42842       10030342.0               Warclav   
8       74360       10049404.0                 Mlobe   
9       78551       10053597.0  Oligocare Forte Plus   
10      78551       10053597.0  Oligocare Forte Plus   
11      81790       10056825.0               Dicewin   
12     107402       10081637.0                Mirtee   
13     117379       10090335.0              Clofiron   
14     117379       10090335.0              Clofiron   
15     117379       10090335.0              Clofiron   
16     117379       10090335.0              Clofiron   
17       1799       10001846.0                 Tiova   
18       2088       10002332.0        Glucored Forte   
19       2088       10002332.0        Glucored Forte   

                                          DisplayName  \
0   Actrapid HM Penfill 100 IU Injection 3 ml Cart...   
1                             Donep M Tablet (10 Tab)   
2                             Donep M Tablet (10 Tab)   
3                           Lidocam Mouth Wash 120 ml   
4                           Lidocam Mouth Wash 120 ml   
5                             Comoist Eye Drops 10 ml   
6                      Warclav 625 mg Tablet (10 Tab)   
7                      Warclav 625 mg Tablet (10 Tab)   
8                             Mlobe Eye Ointment 5 gm   
9                Oligocare Forte Plus Tablet (15 Tab)   
10               Oligocare Forte Plus Tablet (15 Tab)   
11                           Dicewin Capsule (10 Cap)   
12                       Mirtee 30 mg Tablet (10 Tab)   
13                           Clofiron Tablet (10 Tab)   
14                           Clofiron Tablet (10 Tab)   
15                           Clofiron Tablet (10 Tab)   
16                           Clofiron Tablet (10 Tab)   
17                                      Tiova Inhaler   
18                     Glucored Forte Tablet (10 Tab)   
19                     Glucored Forte Tablet (10 Tab)   

                         SaltName                            MfgGroup  \
0   Human Insulin/Soluble Insulin  Abbott India Limited(Novo Nordisk)   
1                       Memantine                  ALKEM LABORATORIES   
2                       Donepezil                  ALKEM LABORATORIES   
3                     Benzoxonium               AJANTA PHARMA LIMITED   
4                       Lidocaine               AJANTA PHARMA LIMITED   
5   Hydroxypropyl Methylcellulose                  KLAR SEHEN PVT LTD   
6                     Amoxycillin                      Pfizer Limited   
7                 Clavulanic Acid                      Pfizer Limited   
8                    Moxifloxacin       Sapient Laboratorises Pvt Ltd   
9                    Coenzyme Q10            Meyer Organics Pvt. Ltd.   
10                    Combination            Meyer Organics Pvt. Ltd.   
11                      Diacerein       T Banko Genic Pharmaceuticals   
12                    Mirtazapine                        TALENT INDIA   
13              Sodium Feredetate             KLOSTER PHARMACEUTICALS   
14                     Folic Acid             KLOSTER PHARMACEUTICALS   
15                    Vitamin B12             KLOSTER PHARMACEUTICALS   
16                 Zinc Gluconate             KLOSTER PHARMACEUTICALS   
17                     Tiotropium                       Cipla Ltd.(M)   
18                  Glibenclamide        Sun Pharma Laboratories Ltd.   
19                      Metformin        Sun Pharma Laboratories Ltd.   

                                    disease_may_treat  \
0                                     

### RxClass API Call for Physiologic Effects information

In [ ]:
pe_map = {}

for index, row in data_df.iterrows():
  if pe_map.__contains__(row["SaltName"]) == False:
    pe_set = set()
    response = request_class(str(row["SaltName"]), 'MEDRT', 'has_pe')
    if response != {}:
      print(response)
      for obj in response['rxclassDrugInfoList']['rxclassDrugInfo']:
        pe_set.add(obj['rxclassMinConceptItem']['className'])
    pe_map[row["SaltName"]]=pe_set

https://rxnav.nlm.nih.gov/REST/rxclass/class/byDrugName.json?drugName=Human%20Insulin/Soluble%20Insulin&relaSource=MEDRT&relas=has_pe
https://rxnav.nlm.nih.gov/REST/rxclass/class/byDrugName.json?drugName=Memantine&relaSource=MEDRT&relas=has_pe
{'rxclassDrugInfoList': {'rxclassDrugInfo': [{'minConcept': {'rxcui': '236685', 'name': 'memantine hydrochloride', 'tty': 'PIN'}, 'rxclassMinConceptItem': {'classId': 'N0000008494', 'className': 'Decreased Central Nervous System Glutamate Activity', 'classType': 'PE'}, 'rela': 'has_pe', 'relaSource': 'MEDRT'}, {'minConcept': {'rxcui': '6719', 'name': 'memantine', 'tty': 'IN'}, 'rxclassMinConceptItem': {'classId': 'N0000008494', 'className': 'Decreased Central Nervous System Glutamate Activity', 'classType': 'PE'}, 'rela': 'has_pe', 'relaSource': 'MEDRT'}]}}
https://rxnav.nlm.nih.gov/REST/rxclass/class/byDrugName.json?drugName=Donepezil&relaSource=MEDRT&relas=has_pe
{'rxclassDrugInfoList': {'rxclassDrugInfo': [{'minConcept': {'rxcui': '135447', 'n

### Populating the Physiologic Effects column using the pe_map

In [ ]:
pe_list = []
for index, row in data_df.iterrows():
  if pe_map.__contains__(row["SaltName"]) == True:
    pe_list.append(pe_map[row["SaltName"]]) 

data_df["Physiologic Effects"] = pe_list

In [ ]:
data_df.head(20)

ProductId  SourceProductId           ProductName  \
0        2607       10002632.0   Actrapid HM Penfill   
1        3447       10003952.0               Donep M   
2        3447       10003952.0               Donep M   
3        8027       10005601.0               Lidocam   
4        8027       10005601.0               Lidocam   
5       14973       10014311.0               Comoist   
6       42842       10030342.0               Warclav   
7       42842       10030342.0               Warclav   
8       74360       10049404.0                 Mlobe   
9       78551       10053597.0  Oligocare Forte Plus   
10      78551       10053597.0  Oligocare Forte Plus   
11      81790       10056825.0               Dicewin   
12     107402       10081637.0                Mirtee   
13     117379       10090335.0              Clofiron   
14     117379       10090335.0              Clofiron   
15     117379       10090335.0              Clofiron   
16     117379       10090335.0              Clofiron   
17       1799       10001846.0                 Tiova   
18       2088       10002332.0        Glucored Forte   
19       2088       10002332.0        Glucored Forte   

                                          DisplayName  \
0   Actrapid HM Penfill 100 IU Injection 3 ml Cart...   
1                             Donep M Tablet (10 Tab)   
2                             Donep M Tablet (10 Tab)   
3                           Lidocam Mouth Wash 120 ml   
4                           Lidocam Mouth Wash 120 ml   
5                             Comoist Eye Drops 10 ml   
6                      Warclav 625 mg Tablet (10 Tab)   
7                      Warclav 625 mg Tablet (10 Tab)   
8                             Mlobe Eye Ointment 5 gm   
9                Oligocare Forte Plus Tablet (15 Tab)   
10               Oligocare Forte Plus Tablet (15 Tab)   
11                           Dicewin Capsule (10 Cap)   
12                       Mirtee 30 mg Tablet (10 Tab)   
13                           Clofiron Tablet (10 Tab)   
14                           Clofiron Tablet (10 Tab)   
15                           Clofiron Tablet (10 Tab)   
16                           Clofiron Tablet (10 Tab)   
17                                      Tiova Inhaler   
18                     Glucored Forte Tablet (10 Tab)   
19                     Glucored Forte Tablet (10 Tab)   

                         SaltName                            MfgGroup  \
0   Human Insulin/Soluble Insulin  Abbott India Limited(Novo Nordisk)   
1                       Memantine                  ALKEM LABORATORIES   
2                       Donepezil                  ALKEM LABORATORIES   
3                     Benzoxonium               AJANTA PHARMA LIMITED   
4                       Lidocaine               AJANTA PHARMA LIMITED   
5   Hydroxypropyl Methylcellulose                  KLAR SEHEN PVT LTD   
6                     Amoxycillin                      Pfizer Limited   
7                 Clavulanic Acid                      Pfizer Limited   
8                    Moxifloxacin       Sapient Laboratorises Pvt Ltd   
9                    Coenzyme Q10            Meyer Organics Pvt. Ltd.   
10                    Combination            Meyer Organics Pvt. Ltd.   
11                      Diacerein       T Banko Genic Pharmaceuticals   
12                    Mirtazapine                        TALENT INDIA   
13              Sodium Feredetate             KLOSTER PHARMACEUTICALS   
14                     Folic Acid             KLOSTER PHARMACEUTICALS   
15                    Vitamin B12             KLOSTER PHARMACEUTICALS   
16                 Zinc Gluconate             KLOSTER PHARMACEUTICALS   
17                     Tiotropium                       Cipla Ltd.(M)   
18                  Glibenclamide        Sun Pharma Laboratories Ltd.   
19                      Metformin        Sun Pharma Laboratories Ltd.   

                                    disease_may_treat  \
0                                     

## Saving the final dataframe to drug_effects.csv

In [ ]:
data_df.to_csv('drug_effects.csv')

## Integrating RxNorm API 

We next integrate the RxNorm API to fetch the RxNorm ID for each salt name. This is needed to invoke the drug interation API. The drug interaction API returns the list of drugs that the input drug adversely interacts with.

In [ ]:
API_REQUEST_RXNORM_ENDPOINT = 'https://rxnav.nlm.nih.gov/'
API_REQUEST_RXNORM_PARAMS = 'REST/rxcui.json?name={value}&search={search}&allsrc=1'

API_LATENCY_ASSUMED = 0.002       # Assuming roughly 2ms latency on the API and network
API_THROTTLE_WAIT = (1.0/100.0)-API_LATENCY_ASSUMED

MEDS_RXNORM_PARAMS_TEMPLATE = {
    "value": "",
    "search":"0"
}

In [ ]:
def rx_norm_request(salt_name,
                  endpoint_url = API_REQUEST_RXNORM_ENDPOINT, 
                  endpoint_params = API_REQUEST_RXNORM_PARAMS,
                  request_template = MEDS_RXNORM_PARAMS_TEMPLATE):
    # Make sure we have an article title
    if not salt_name: 
      print ("NO name")
      return None
    
    # Titles are supposed to have spaces replaced with "_" and be URL encoded
    salt_name_encoded = salt_name.replace(' ','%20')
    request_template['value'] = salt_name_encoded
    
    # now, create a request URL by combining the endpoint_url with the parameters for the request
    request_url = endpoint_url+endpoint_params.format(**request_template)
    print(request_url)
    
    # make the request
    try:
        # we'll wait first, to make sure we don't exceed the limit in the situation where an exception
        # occurs during the request processing - throttling is always a good practice with a free
        # data source like Wikipedia - or other community sources
        if API_THROTTLE_WAIT > 0.0:
            time.sleep(API_THROTTLE_WAIT)
        response = requests.get(request_url)
        json_response = response.json()
        
    except Exception as e:
        print(e)
        json_response = None
    return json_response

In [ ]:
response = rx_norm_request('Rizatriptan')

https://rxnav.nlm.nih.gov/REST/rxcui.json?name=Rizatriptan&search=0&allsrc=1


In [ ]:
response

{'idGroup': {'rxnormId': ['88014']}}

In [ ]:
response['idGroup']['rxnormId'][0]

'88014'

## Integrating Drug Interaction API

In [ ]:
API_REQUEST_INTERACTION_ENDPOINT = 'https://rxnav.nlm.nih.gov/'
API_REQUEST_INTERACTION_PARAMS = 'REST/interaction/interaction.json?rxcui={rxcui}&sources={sources}'

API_LATENCY_ASSUMED = 0.002       # Assuming roughly 2ms latency on the API and network
API_THROTTLE_WAIT = (1.0/100.0)-API_LATENCY_ASSUMED

MEDS_INTERACTION_PARAMS_TEMPLATE = {
    "rxcui": "",
    "sources":"ONCHigh"
}

In [ ]:
def drug_interaction_request(rxcui,
                  endpoint_url = API_REQUEST_INTERACTION_ENDPOINT, 
                  endpoint_params = API_REQUEST_INTERACTION_PARAMS,
                  request_template = MEDS_INTERACTION_PARAMS_TEMPLATE):
    # Make sure we have an article title
    if not rxcui: 
      print ("NO name")
      return None
    
    # Titles are supposed to have spaces replaced with "_" and be URL encoded
    request_template['rxcui'] = rxcui
    
    # now, create a request URL by combining the endpoint_url with the parameters for the request
    request_url = endpoint_url+endpoint_params.format(**request_template)
    print(request_url)
    
    # make the request
    try:
        # we'll wait first, to make sure we don't exceed the limit in the situation where an exception
        # occurs during the request processing - throttling is always a good practice with a free
        # data source like Wikipedia - or other community sources
        if API_THROTTLE_WAIT > 0.0:
            time.sleep(API_THROTTLE_WAIT)
        response = requests.get(request_url)
        json_response = response.json()
        
    except Exception as e:
        print(e)
        json_response = None
    return json_response

In [ ]:
drug_interaction_response = drug_interaction_request('25789')

https://rxnav.nlm.nih.gov/REST/interaction/interaction.json?rxcui=25789&sources=ONCHigh


In [ ]:
data_df = pd.read_csv("/content/catalog_data.csv", on_bad_lines='skip')

### Getting RxCUI for each salt name in the catalog

In [ ]:
rxcui_map = {}

for index, row in data_df.iterrows():
  if rxcui_map.__contains__(row["SaltName"]) == False:
    rxcui = rx_norm_request(str(row["SaltName"]))
    if rxcui != {}:
      if 'rxnormId' in rxcui['idGroup']:
        rxcui_map[row["SaltName"]]=rxcui['idGroup']['rxnormId'][0]

Streaming output truncated to the last 5000 lines.
https://rxnav.nlm.nih.gov/REST/rxcui.json?name=Ankle%20Support&search=0&allsrc=1
https://rxnav.nlm.nih.gov/REST/rxcui.json?name=Hot%20Bag&search=0&allsrc=1
https://rxnav.nlm.nih.gov/REST/rxcui.json?name=Scrubs&search=0&allsrc=1
https://rxnav.nlm.nih.gov/REST/rxcui.json?name=Moisturising%20Creams%20&%20Lotions&search=0&allsrc=1
https://rxnav.nlm.nih.gov/REST/rxcui.json?name=Tooth%20Pastes&search=0&allsrc=1
https://rxnav.nlm.nih.gov/REST/rxcui.json?name=Hair%20Colours%20&%20Dyes&search=0&allsrc=1
https://rxnav.nlm.nih.gov/REST/rxcui.json?name=Feminine%20Beauty%20Talc&search=0&allsrc=1
https://rxnav.nlm.nih.gov/REST/rxcui.json?name=Baby%20Massage%20Oil&search=0&allsrc=1
https://rxnav.nlm.nih.gov/REST/rxcui.json?name=Feeding%20Bottle&search=0&allsrc=1
https://rxnav.nlm.nih.gov/REST/rxcui.json?name=Feminine%20Face%20Packs&search=0&allsrc=1
https://rxnav.nlm.nih.gov/REST/rxcui.json?name=Baby%20Diapers&search=0&allsrc=1
https://rxnav.nlm.nih.

We create the drug interaction map by passing the RxCUI each each salt in the salt map to the drug-interaction API. This, we store the list of drug interactions corresponding to each salt.

In [ ]:
drug_interaction_map = {}

for index, row in data_df.iterrows():
  if drug_interaction_map.__contains__(row["SaltName"]) == False:
    drug_interaction = set()
    if row["SaltName"] in rxcui_map:
      drug_interaction_response = drug_interaction_request(rxcui_map[row["SaltName"]])
      if drug_interaction_response != None:
        if 'interactionTypeGroup' in drug_interaction_response:
          for obj in drug_interaction_response['interactionTypeGroup'][0]['interactionType'][0]['interactionPair']:
            drug_interaction.add(obj['interactionConcept'][1]['minConceptItem']['name'])
    drug_interaction_map[row["SaltName"]]=drug_interaction

https://rxnav.nlm.nih.gov/REST/interaction/interaction.json?rxcui=10582&sources=ONCHigh
https://rxnav.nlm.nih.gov/REST/interaction/interaction.json?rxcui=1446906&sources=ONCHigh
https://rxnav.nlm.nih.gov/REST/interaction/interaction.json?rxcui=6809&sources=ONCHigh
https://rxnav.nlm.nih.gov/REST/interaction/interaction.json?rxcui=31555&sources=ONCHigh
https://rxnav.nlm.nih.gov/REST/interaction/interaction.json?rxcui=17767&sources=ONCHigh
https://rxnav.nlm.nih.gov/REST/interaction/interaction.json?rxcui=73494&sources=ONCHigh
https://rxnav.nlm.nih.gov/REST/interaction/interaction.json?rxcui=2409&sources=ONCHigh
https://rxnav.nlm.nih.gov/REST/interaction/interaction.json?rxcui=5487&sources=ONCHigh
https://rxnav.nlm.nih.gov/REST/interaction/interaction.json?rxcui=1482680&sources=ONCHigh
https://rxnav.nlm.nih.gov/REST/interaction/interaction.json?rxcui=61381&sources=ONCHigh
https://rxnav.nlm.nih.gov/REST/interaction/interaction.json?rxcui=187832&sources=ONCHigh
https://rxnav.nlm.nih.gov/REST

In [ ]:
drug_interaction_map

{'Thyroxine': set(),
 'Teneligliptin': set(),
 'Metformin': set(),
 'Nebivolol': set(),
 'Amlodipine': set(),
 'Telmisartan': set(),
 'Chlorthalidone': set(),
 'Hydrochlorothiazide': set(),
 'Luliconazole': set(),
 'Olanzapine': set(),
 'Pregabalin': set(),
 'Mecobalamin': set(),
 'Folic Acid': set(),
 'Pyridoxine': set(),
 'Benfotiamine': set(),
 'Itraconazole': {'dihydroergotamine',
  'ergonovine',
  'ergotamine',
  'irinotecan',
  'lovastatin',
  'methylergonovine',
  'simvastatin'},
 'Nortriptyline': {'isocarboxazid',
  'phenelzine',
  'procarbazine',
  'selegiline',
  'tranylcypromine'},
 'Torsemide': set(),
 'Clopidogrel': set(),
 'Rosuvastatin': set(),
 'Methylcobalamin': set(),
 'Levocarnitine': set(),
 'Levetiracetam': set(),
 'Allopurinol': set(),
 'Glimepiride': set(),
 'Olmesartan': set(),
 'Domperidone': {'aclarubicin',
  'amiodarone',
  'anagrelide',
  'arsenic trioxide',
  'astemizole',
  'azithromycin',
  'bepridil',
  'cesium chloride',
  'chloroquine',
  'chlorpromazi

In [ ]:
rxcui_map

{'Thyroxine Sodium': '10582',
 'Teneligliptin': '1446906',
 'Metformin': '6809',
 'Nebivolol': '31555',
 'Amlodipine': '17767',
 'Telmisartan': '73494',
 'Chlorthalidone': '2409',
 'Hydrochlorothiazide': '5487',
 'Luliconazole': '1482680',
 'Olanzapine': '61381',
 'Pregabalin': '187832',
 'Mecobalamin': '29421',
 'Pyridoxine': '1551665',
 'Benfotiamine': '18891',
 'Itraconazole': '28031',
 'Nortriptyline': '7531',
 'Torsemide': '38413',
 'Clopidogrel': '32968',
 'Rosuvastatin': '301542',
 'Methylcobalamin': '29421',
 'Levocarnitine': '42955',
 'Levetiracetam': '114477',
 'Allopurinol': '519',
 'Glimepiride': '25789',
 'Olmesartan': '321064',
 'Domperidone': '3626',
 'Pantoprazole': '40790',
 'Sertaconazole': '36435',
 'Eberconazole': '233940',
 'Terbinafine': '37801',
 'Ketoconazole': '6135',
 'Piracetam': '8351',
 'Salbutamol': '435',
 'Ambroxol': '625',
 'Atorvastatin': '83367',
 'Aspirin': '1191',
 'Minoxidil': '6984',
 'Propranolol': '8787',
 'Levosulpiride': '68382',
 'Prucaloprid

In [ ]:
interaction_drugs = []
rxcui = []
for index, row in data_df.iterrows():
  if drug_interaction_map.__contains__(row["SaltName"]) == True:
    interaction_drugs.append(drug_interaction_map[row["SaltName"]]) 
  else:
    interaction_drugs.append('')
  if rxcui_map.__contains__(row["SaltName"]) == True:
    rxcui.append(rxcui_map[row["SaltName"]])
  else:
    rxcui.append('')

data_df["rxcui"] = rxcui
data_df["drug_interactions"] = interaction_drugs

In [ ]:
data_df.head(20)

link  \
0   https://drive.google.com/file/d/1bytgW52eg1MLO...   
1   https://drive.google.com/file/d/1pXQw9tQ74mzMO...   
2   https://drive.google.com/file/d/1pXQw9tQ74mzMO...   
3   https://drive.google.com/file/d/1LV1JxnTMSmiJ1...   
4   https://drive.google.com/file/d/1LV1JxnTMSmiJ1...   
5   https://drive.google.com/file/d/1l7oVPwM6ds-2C...   
6   https://drive.google.com/file/d/1l7oVPwM6ds-2C...   
7   https://drive.google.com/file/d/1l3NEQ0t0DJ_uD...   
8   https://drive.google.com/file/d/1l3NEQ0t0DJ_uD...   
9   https://drive.google.com/file/d/1l3NEQ0t0DJ_uD...   
10  https://drive.google.com/file/d/10rxUlnov56rMA...   
11  https://drive.google.com/file/d/1JFdBmMp1UrbkC...   
12  https://drive.google.com/file/d/13AddzX_IOlF16...   
13  https://drive.google.com/file/d/13AddzX_IOlF16...   
14  https://drive.google.com/file/d/13AddzX_IOlF16...   
15  https://drive.google.com/file/d/13AddzX_IOlF16...   
16  https://drive.google.com/file/d/13AddzX_IOlF16...   
17  https://drive.google.com/file/d/1xCpdp-V-RdasW...   
18  https://drive.google.com/file/d/1NN53kx6NjJ7uL...   
19  https://drive.google.com/file/d/1y-WlHDOFz_vH-...   

                                               img_fp  ProductId  \
0   ../data/uploaded_junk/Medicine box- images of ...      47442   
1   ../data/uploaded_junk/Medicine box- images of ...      71764   
2   ../data/uploaded_junk/Medicine box- images of ...      71764   
3   ../data/uploaded_junk/Medicine box- images of ...       6348   
4   ../data/uploaded_junk/Medicine box- images of ...       6348   
5   ../data/uploaded_junk/Medicine box- images of ...      47720   
6   ../data/uploaded_junk/Medicine box- images of ...      47720   
7   ../data/uploaded_junk/Medicine box- images of ...      18497   
8   ../data/uploaded_junk/Medicine box- images of ...      18497   
9   ../data/uploaded_junk/Medicine box- images of ...      18497   
10  ../data/uploaded_junk/Medicine box- images of ...      68608   
11  ../data/uploaded_junk/Medicine box- images of ...      13328   
12  ../data/uploaded_junk/Medicine box- images of ...      88978   
13  ../data/uploaded_junk/Medicine box- images of ...      88978   
14  ../data/uploaded_junk/Medicine box- images of ...      88978   
15  ../data/uploaded_junk/Medicine box- images of ...      88978   
16  ../data/uploaded_junk/Medicine box- images of ...      88978   
17  ../data/uploaded_junk/Medicine box- images of ...       1491   
18  ../data/uploaded_junk/Medicine box- images of ...      77424   
19  ../data/uploaded_junk/Medicine box- images of ...      24395   

                                     DisplayName     ProductName  \
0              Thyronorm 50 mcg Tablet (120 Tab)       Thyronorm   
1              Olymprix M 500 mg Tablet (15 Tab)      Olymprix M   
2              Olymprix M 500 mg Tablet (15 Tab)      Olymprix M   
3                        Nebi AM Tablet (10 Tab)         Nebi AM   
4                        Nebi AM Tablet (10 Tab)         Nebi AM   
5           Tellzy CH 40/6.25 mg Tablet (15 Tab)       Tellzy CH   
6           Tellzy CH 40/6.25 mg Tablet (15 Tab)       Tellzy CH   
7                Telma Amh 40 mg Tablet (15 Tab)       Telma Amh   
8                Telma Amh 40 mg Tablet (15 Tab)       Telma Amh   
9                Telma Amh 40 mg Tablet (15 Tab)       Telma Amh   
10                          LuliDerm Cream 10 gm        LuliDerm   
11                  Olimelt 5 mg Tablet (10 Tab)         Olimelt   
12  Benalgis Forte Soft Gelatin Capsule (15 Cap)  Benalgis Forte   
13  Benalgis Forte Soft Gelatin Capsule (15 Cap)  Benalgis Forte   
14  Benalgis Forte Soft Gelatin Capsule (15 Cap)  Benalgis Forte   
15  Benalgis Forte Soft Gelatin Capsule (15 Cap)  Benalgis Forte   
16  Benalgis Forte Soft Gelatin Capsule (15 Cap)  Benalgis Forte   
17                  Tellzy 40 mg Tablet (10 Tab)          Tellzy   
18             Candiforce 200 mg Capsule (7 Cap)      Candiforce   
19                    Nortipan M Tablet (10 Tab)      Nortipan

In [ ]:
data_df.to_csv('drug_interactions.csv')

In [ ]:
data_df = pd.read_csv("/content/salts_separated.csv")

In [ ]:
data_df.head()

link  \
0  https://drive.google.com/file/d/1bytgW52eg1MLO...   
1  https://drive.google.com/file/d/1pXQw9tQ74mzMO...   
2  https://drive.google.com/file/d/1pXQw9tQ74mzMO...   
3  https://drive.google.com/file/d/1LV1JxnTMSmiJ1...   
4  https://drive.google.com/file/d/1LV1JxnTMSmiJ1...   

                                              img_fp  ProductId  \
0  ../data/uploaded_junk/Medicine box- images of ...      47442   
1  ../data/uploaded_junk/Medicine box- images of ...      71764   
2  ../data/uploaded_junk/Medicine box- images of ...      71764   
3  ../data/uploaded_junk/Medicine box- images of ...       6348   
4  ../data/uploaded_junk/Medicine box- images of ...       6348   

                         DisplayName ProductName  \
0  Thyronorm 50 mcg Tablet (120 Tab)   Thyronorm   
1  Olymprix M 500 mg Tablet (15 Tab)  Olymprix M   
2  Olymprix M 500 mg Tablet (15 Tab)  Olymprix M   
3            Nebi AM Tablet (10 Tab)     Nebi AM   
4            Nebi AM Tablet (10 Tab)     Nebi AM   

                                     MfgGroup       SaltName       Strength  \
0                        Abbott India Limited      Thyroxine  50 mcg Tablet   
1                     Alkem Laboratories Ltd.  Teneligliptin  500 mg Tablet   
2                     Alkem Laboratories Ltd.      Metformin  500 mg Tablet   
3  Aristo Pharmaceuticals Private Limited.(M)      Nebivolol         Tablet   
4  Aristo Pharmaceuticals Private Limited.(M)     Amlodipine         Tablet   

                                               query  
0  12:05 pma al ... thyroxine sodium tablets thyr...  
1  each sege olympro erelion tabler ne hy औलमप्रक...  
2  each sege olympro erelion tabler ne hy औलमप्रक...  
3  colour lake quinoline dosage: keep keep out of...  
4  colour lake quinoline dosage: keep keep out of...

Calculating the number of populated fields out of total FileLinks

In [3]:
data_df_generated = pd.read_csv("/content/drug_effects_catalog_data.csv", on_bad_lines='skip')

In [4]:
data_df_generated.head()

Unnamed: 0  ProductId  SourceProductId          ProductName  \
0           0       2607       10002632.0  Actrapid HM Penfill   
1           1       3447       10003952.0              Donep M   
2           2       3447       10003952.0              Donep M   
3           3       8027       10005601.0              Lidocam   
4           4       8027       10005601.0              Lidocam   

                                         DisplayName  \
0  Actrapid HM Penfill 100 IU Injection 3 ml Cart...   
1                            Donep M Tablet (10 Tab)   
2                            Donep M Tablet (10 Tab)   
3                          Lidocam Mouth Wash 120 ml   
4                          Lidocam Mouth Wash 120 ml   

                        SaltName                            MfgGroup  \
0  Human Insulin/Soluble Insulin  Abbott India Limited(Novo Nordisk)   
1                      Memantine                  ALKEM LABORATORIES   
2                      Donepezil                  ALKEM LABORATORIES   
3                    Benzoxonium               AJANTA PHARMA LIMITED   
4                      Lidocaine               AJANTA PHARMA LIMITED   

                                   disease_may_treat  \
0                                              set()   
1                              {'Alzheimer Disease'}   
2                              {'Alzheimer Disease'}   
3                                              set()   
4  {'Pain', 'Burns', 'Tachycardia, Ventricular', ...   

                                                 atc  \
0                                              set()   
1  {'Other anti-dementia drugs', 'Anticholinester...   
2                            {'Anticholinesterases'}   
3  {'Antiinfectives and antiseptics for local ora...   
4  {'Local anesthetics', 'Analgesics and anesthet...   

                             Pharmacological Actions  \
0                                              set()   
1  {'Dopamine Agents', 'Antiparkinson Agents', 'E...   
2  {'Nootropic Agents', 'Cholinesterase Inhibitors'}   
3                                              set()   
4  {'Anesthetics, Local', 'Voltage-Gated Sodium C...   

                                 Physiologic Effects  
0                                              set()  
1  {'Decreased Central Nervous System Glutamate A...  
2  {'Increased Central Nervous System Acetylcholi...  
3                                              set()  
4  {'Decreased Sensory-Somatic Nervous System Org...

In [16]:
product = []
rows_with_no_information = 0
for index, row in data_df_generated.iterrows():
  if row["disease_may_treat"] == "set()" and row["atc"] == "set()" and row["Pharmacological Actions"] == "set()" and row["Physiologic Effects"] == "set()":
    rows_with_no_information = rows_with_no_information+1
    product.append(row["ProductName"])

print(rows_with_no_information)



75086
